# Session 9a - Using Bert-style models for Cultural Data Science

[*NB: Much of this notebook is taken directly from the documentation for the package ```BERTopic``` which we're working with today. You can find more at the website [here](https://maartengr.github.io/BERTopic/index.html) and at the [Github repo](https://github.com/MaartenGr/BERTopic)*]

In this tutorial we will be exploring how to use BERTopic to create topics from the well-known [20Newsgroups dataset](http://qwone.com/~jason/20Newsgroups/). The most frequent use-cases and methods are discussed together with important parameters to keep a look out for. 


## BERTopic
BERTopic is a topic modeling technique that leverages 🤗 transformers and a custom class-based TF-IDF to create dense clusters allowing for easily interpretable topics whilst keeping important words in the topic descriptions. 

<br>

<img src="https://raw.githubusercontent.com/MaartenGr/BERTopic/master/images/logo.png" width="40%">

# Data
For this example, we use the popular 20 Newsgroups dataset which contains roughly 18000 posts from an old online news forum.

In [1]:
import os
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.datasets import fetch_20newsgroups
from bertopic import BERTopic

/opt/homebrew/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
docs = fetch_20newsgroups(subset='all',  
                          remove=('headers', 'footers', 'quotes'))['data']

# **Topic Modeling**

In this example, we will go through the main components of BERTopic and the steps necessary to create a strong topic model. 

**NB:** This will take a long time to run! We'll use a pre-trained version below.



## Training

We start by instantiating BERTopic. We set language to `english` since our documents are in the English language.

We will also calculate the topic probabilities. However, this can slow down BERTopic significantly at large amounts of data (>100_000 documents). It is advised to turn this off if you want to speed up the model. 


In [ ]:
# initialize the model
topic_model = BERTopic(language="english", 
                       calculate_probabilities=True, 
                       verbose=True)

# notice how we use the same fit_transform logic as we've seen before
topics, probs = topic_model.fit_transform(docs)

**NOTE**: Use `language="multilingual"` to select a model that support 50+ languages.

# **Model loading and saving**
The model and most of its internal settings can easily be saved and reused later:

In [ ]:
# Save model
#topic_model.save("teaching_model")	

In [2]:
# Load model
topic_model = BERTopic.load("teaching_model")	

## Extracting Topics
After fitting our model, we can start by looking at the results. Typically, we look at the most frequent topics first as they best represent the collection of documents. 

In [3]:
freq = topic_model.get_topic_info()
freq.head(10)

Topic  Count                             Name  \
0     -1   6713                  -1_to_the_is_of   
1      0   1831             0_game_team_games_he   
2      1    593    1_key_clipper_chip_encryption   
3      2    524             2_ites_cheek_yep_huh   
4      3    451       3_israel_israeli_jews_arab   
5      4    441          4_drive_scsi_drives_ide   
6      5    310           5_car_cars_engine_ford   
7      6    283  6_health_newsgroup_cancer_email   
8      7    259            7_bike_riding_ride_my   
9      8    175   8_space_launch_station_shuttle   

                                      Representation  \
0     [to, the, is, of, and, you, for, that, it, in]   
1  [game, team, games, he, players, season, hocke...   
2  [key, clipper, chip, encryption, keys, escrow,...   
3    [ites, cheek, yep, huh, ken, why, each, of, , ]   
4  [israel, israeli, jews, arab, arabs, jewish, p...   
5  [drive, scsi, drives, ide, disk, controller, h...   
6  [car, cars, engine, ford, miles, toyota, musta...   
7  [health, newsgroup, cancer, email, 1993, disea...   
8  [bike, riding, ride, my, lane, car, you, passe...   
9  [space, launch, station, shuttle, nasa, moon, ...   

                                 Representative_Docs  
0  [\nThat was my point. If I play poker with Mon...  
1  [The FLYERS team that can beat any team on any...  
2  [I have an idea as to why the encryption algor...  
3  [\nHuh?, \nYep.\n, \n \n                      ...  
4  [From: Center for Policy Research <cpr>\nSubje...  
5  [\n[ First of all, please edit your postings. ...  
6  [\nWhile I don't read normally read this group...  
7  [*********************************************...  
8  [\nI'll tell you my story as an example of wha...  
9  [NASA Headquarters distributed the following p...

-1 refers to all outliers and should typically be ignored. Next, let's take a look at a frequent topic that were generated:

In [5]:
topic_model.get_topic(8)  # Select the most frequent topic

[('space', 0.019782595271995225),
 ('launch', 0.016346720702702836),
 ('station', 0.009501978858008736),
 ('shuttle', 0.008605214035740636),
 ('nasa', 0.008230133803979524),
 ('moon', 0.007928205445813595),
 ('redesign', 0.007411693495579464),
 ('commercial', 0.00655678591626107),
 ('billion', 0.006220525573405813),
 ('lunar', 0.006162872781191492)]

**NOTE**: BERTopic is stocastich which mmeans that the topics might differ across runs. This is mostly due to the stocastisch nature of UMAP.

## Attributes

There are a number of attributes that you can access after having trained your BERTopic model:


| Attribute | Description |
|------------------------|---------------------------------------------------------------------------------------------|
| topics_               | The topics that are generated for each document after training or updating the topic model. |
| probabilities_ | The probabilities that are generated for each document if HDBSCAN is used. |
| topic_sizes_           | The size of each topic                                                                      |
| topic_mapper_          | A class for tracking topics and their mappings anytime they are merged/reduced.             |
| topic_representations_ | The top *n* terms per topic and their respective c-TF-IDF values.                             |
| c_tf_idf_              | The topic-term matrix as calculated through c-TF-IDF.                                       |
| topic_labels_          | The default labels for each topic.                                                          |
| custom_labels_         | Custom labels for each topic as generated through `.set_topic_labels`.                                                               |
| topic_embeddings_      | The embeddings for each topic if `embedding_model` was used.                                                              |
| representative_docs_   | The representative documents for each topic if HDBSCAN is used.                                                |

For example, to access the predicted topics for the first 10 documents, we simply run the following:

In [6]:
topic_model.topics_[:10]

[0, -1, 58, 4, 100, -1, 64, 0, 0, -1]

# **Visualization**
There are several visualization options available in BERTopic, namely the visualization of topics, probabilities and topics over time. Topic modeling is, to a certain extent, quite subjective. Visualizations help understand the topics that were created. 

## Visualize Topics
After having trained our `BERTopic` model, we can iteratively go through perhaps a hundred topic to get a good 
understanding of the topics that were extract. However, that takes quite some time and lacks a global representation. 
Instead, we can visualize the topics that were generated in a way very similar to 
[LDAvis](https://github.com/cpsievert/LDAvis):

In [7]:
topic_model.visualize_topics()

## Visualize Topic Probabilities

The variable `probabilities` that is returned from `transform()` or `fit_transform()` can 
be used to understand how confident BERTopic is that certain topics can be found in a document. 

To visualize the distributions, we simply call:

In [8]:
topic_model.visualize_distribution(probs[100])

NameError: name 'probs' is not defined

## Visualize Topic Hierarchy

The topics that were created can be hierarchically reduced. In order to understand the potential hierarchical structure of the topics, we can use scipy.cluster.hierarchy to create clusters and visualize how they relate to one another. This might help selecting an appropriate nr_topics when reducing the number of topics that you have created.

In [9]:
topic_model.visualize_hierarchy(top_n_topics=50)

## Visualize Terms

We can visualize the selected terms for a few topics by creating bar charts out of the c-TF-IDF scores for each topic representation. Insights can be gained from the relative c-TF-IDF scores between and within topics. Moreover, you can easily compare topic representations to each other.

In [10]:
topic_model.visualize_barchart(top_n_topics=20)

## Visualize Topic Similarity
Having generated topic embeddings, through both c-TF-IDF and embeddings, we can create a similarity matrix by simply applying cosine similarities through those topic embeddings. The result will be a matrix indicating how similar certain topics are to each other.

In [11]:
topic_model.visualize_heatmap(n_clusters=20, 
                              width=1000, 
                              height=1000)

# **Search Topics**
After having trained our model, we can use `find_topics` to search for topics that are similar 
to an input search_term. Here, we are going to be searching for topics that closely relate the 
search term "vehicle". Then, we extract the most similar topic and check the results: 

In [12]:
similar_topics, similarity = topic_model.find_topics("vehicle", top_n=5)
print(similar_topics)

[5, 7, 147, 15, 61]


In [13]:
topic_model.get_topic(5)

[('car', 0.02458286077916575),
 ('cars', 0.013452123311089723),
 ('engine', 0.012435195126102461),
 ('ford', 0.011541926672969816),
 ('miles', 0.008542015475094611),
 ('toyota', 0.008533918377672322),
 ('mustang', 0.008405914235024823),
 ('v8', 0.007118294256299153),
 ('sho', 0.005990744998274382),
 ('v6', 0.005970335817740334)]

In [16]:
print(topic_model.get_representative_docs(5)[0])


While I don't read normally read this group, I was looking for Valentine radar
information (sigh, maybe in the FAQ) and came across your posting..

I bought a '93 Probe GT with the PEP 263A last July (now at 9500 miles)
after debating over the Sentra SE-R/NX2000, MX6, MR-2, Stealth, Prelude, 
and Celica.

Check this month's Consumer Reports for previous Probe records.  

My criteria: a "fun" car with ABS, airbag, over 130hp, and less than $25K.
I thought about a turbo, but checking with insurance people ruled that out.
The Tri-Star cars (Eclipse/Talon/etc) were out since they don't have an air bag.
Ditto for the Mustang(also no ABS).
The SE-R/NX2000/M20 fell into the pocket-rocket category.  A good used car buy.
The MX-6 was almost there but rolled more than I liked.  
I didn't like the Prelude dash/instrumentation at all.  Too weird for me.
The MR2 has a much smaller non-passenger space than I needed, so out that went.
The Celica was "ok" but underpowered when loaded with options (an